<a href="https://colab.research.google.com/github/pachterlab/LSCHWCP_2023/blob/main/Notebooks/Figure_3/Figure_3b/2_validate_palmdb2palmdb_visualization.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Validate the alignment of RdRP nucleotide sequences to the corresponding amino acid references with kallisto translated search - Part 2/2: Visualize results

In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
%config InlineBackend.figure_format='retina'

Download alignment results generated [here](https://github.com/pachterlab/LSCHWCP_2023/blob/main/Notebooks/Figure_3/Figure_3b/1_validate_palmdb2palmdb_alignment.ipynb):

In [2]:
!wget https://raw.githubusercontent.com/pachterlab/LSCHWCP_2023/refs/heads/main/Notebooks/Figure_3/Figure_3b/phylum_mapping.csv
!wget https://raw.githubusercontent.com/pachterlab/LSCHWCP_2023/refs/heads/main/Notebooks/Figure_3/Figure_3b/class_mapping.csv
!wget https://raw.githubusercontent.com/pachterlab/LSCHWCP_2023/refs/heads/main/Notebooks/Figure_3/Figure_3b/family_mapping.csv
!wget https://raw.githubusercontent.com/pachterlab/LSCHWCP_2023/refs/heads/main/Notebooks/Figure_3/Figure_3b/order_mapping.csv
!wget https://raw.githubusercontent.com/pachterlab/LSCHWCP_2023/refs/heads/main/Notebooks/Figure_3/Figure_3b/genus_mapping.csv
!wget https://raw.githubusercontent.com/pachterlab/LSCHWCP_2023/refs/heads/main/Notebooks/Figure_3/Figure_3b/species_mapping.csv

--2024-12-02 18:15:51--  https://raw.githubusercontent.com/pachterlab/LSCHWCP_2023/refs/heads/main/Notebooks/Figure_3/Figure_3b/phylum_mapping.csv
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.111.133, 185.199.109.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.111.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 311 [text/plain]
Saving to: ‘phylum_mapping.csv’

phylum_mapping.csv  100%[===================>]     311  --.-KB/s    in 0s      

2024-12-02 18:15:52 (2.68 MB/s) - ‘phylum_mapping.csv’ saved [311/311]

--2024-12-02 18:15:52--  https://raw.githubusercontent.com/pachterlab/LSCHWCP_2023/refs/heads/main/Notebooks/Figure_3/Figure_3b/class_mapping.csv
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.111.133, 185.199.108.133, 185.199.109.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.111.133|:443... connected.

Plot:

In [3]:
def fractions(df):
    m_types = df["mapping"].values

    # # Drop unknown virus sequences and transpose dataframe
    # df_T = df.drop(".", axis=1).set_index("mapping").T
    # Transpose dataframe
    df_T = df.set_index("mapping").T

    # Add total
    df_T["total"] = df_T.sum(axis=1).values

    # Compute fraction of total count for each mapping type
    for mt in m_types:
        df_T[f"{mt}_fraction"] = (df_T[mt] / df_T["total"]).values

    return df_T

In [4]:
fig, axs = plt.subplots(figsize=(100, 20), ncols=5)

fontsize = 50
subplt_spacing = 0.04

colors = ["#3e8938", "red", "grey", "lightgrey"]
alphas = [0.75, 1, 1, 1]
m_types = ["correct", "incorrect", "not_aligned", "multimapped"]
legend_labels = ["Correct", "Incorrect", "Not aligned", "Multimapped"]

## Plot phylum fractions
phyla_df = pd.read_csv("phylum_mapping.csv")
frac_df = fractions(phyla_df)
x = list(map(lambda st: str.replace(st, ".", "Unknown"), frac_df.index.values))
ax = axs[0]

previous_samples = 0
for alpha, color, mt in zip(alphas, colors, m_types):
    y = frac_df[f"{mt}_fraction"].values
    ax.bar(
        x,
        y,
        width = 0.75,
        bottom = previous_samples,
        color = color,
        alpha = alpha,
    )
    previous_samples = previous_samples + y

# Add number of sequences above each bar
for index, total in enumerate(frac_df["total"].values):
    ax.text(x=index, y=1.01, s="{:,}".format(total), size=fontsize, ha="left", rotation=45)

ax.set_xticklabels(x, rotation=45, ha="right")
ax.tick_params(axis="both", labelsize=fontsize)
ax.margins(x=subplt_spacing, y=0)
ax.spines[['right']].set_visible(False)
ax.patch.set_alpha(0)

ax.set_ylabel("Fraction", fontsize=fontsize+2)

# Add '# sequences' label
ax.text(-0.8, 1.01, "# sequences", fontsize=fontsize, ha="left", rotation=45)

## Plot class fractions
class_df = pd.read_csv("class_mapping.csv")
frac_df = fractions(class_df)
x = list(map(lambda st: str.replace(st, ".", "Unknown"), frac_df.index.values))
ax = axs[1]

previous_samples = 0
for alpha, color, mt in zip(alphas, colors, m_types):
    y = frac_df[f"{mt}_fraction"].values
    ax.bar(
        x,
        y,
        width = 0.75,
        bottom = previous_samples,
        color = color,
        alpha = alpha,
    )
    previous_samples = previous_samples + y

# Add number of sequences above each bar
for index, total in enumerate(frac_df["total"].values):
    ax.text(x=index, y=1.01, s="{:,}".format(total), size=fontsize - 15, ha="left", rotation=45)

ax.set_xticklabels(x, rotation=45, ha="right")
ax.tick_params(axis="both", labelsize=fontsize - 15)
ax.margins(x=subplt_spacing, y=0)
ax.spines[['left', 'right']].set_visible(False)
ax.set_yticks([])
ax.patch.set_alpha(0)


## Plot order fractions
order_df = pd.read_csv("order_mapping.csv")
frac_df = fractions(order_df)
x = list(map(lambda st: str.replace(st, ".", "Unknown"), frac_df.index.values))
ax = axs[2]

previous_samples = 0
for alpha, color, mt in zip(alphas, colors, m_types):
    y = frac_df[f"{mt}_fraction"].values
    ax.bar(
        x,
        y,
        width = 0.75,
        bottom = previous_samples,
        color = color,
        alpha = alpha,
    )
    previous_samples = previous_samples + y

# Add number of sequences above each bar
for index, total in enumerate(frac_df["total"].values):
    ax.text(x=index, y=1.01, s="{:,}".format(total), size=fontsize - 25, ha="left", rotation=45)

ax.set_xticklabels(x, rotation=45, ha="right")
ax.tick_params(axis="both", labelsize=fontsize - 25)
ax.margins(x=subplt_spacing, y=0)
ax.spines[['left', 'right']].set_visible(False)
ax.set_yticks([])
ax.patch.set_alpha(0)

## Plot family fractions
family_df = pd.read_csv("family_mapping.csv")
frac_df = fractions(family_df)
x = list(map(lambda st: str.replace(st, ".", "Unknown"), frac_df.index.values))
ax = axs[3]

previous_samples = 0
for alpha, color, mt in zip(alphas, colors, m_types):
    y = frac_df[f"{mt}_fraction"].values
    ax.bar(
        x,
        y,
        width = 1,
        bottom = previous_samples,
        color = color,
        alpha = alpha,
    )
    previous_samples = previous_samples + y

ax.xaxis.set_tick_params(labelbottom=False)
ax.yaxis.set_tick_params(labelleft=False)
ax.margins(x=subplt_spacing, y=0)
ax.spines[['left', 'right']].set_visible(False)
ax.set_xticks([])
ax.set_yticks([])
ax.patch.set_alpha(0)

## Plot genus and species fractions
genus_df = pd.read_csv("genus_mapping.csv")
species_df = pd.read_csv("species_mapping.csv")

# Combine genus and species dataframe since there are too many taxa in each category to plot separately
combined_df = pd.DataFrame()
combined_df["genus"] = genus_df.set_index("mapping").sum(axis=1).values
combined_df["species"] = species_df.set_index("mapping").sum(axis=1).values
combined_df["mapping"] = species_df["mapping"].values

frac_df = fractions(combined_df)
x = list(map(lambda st: str.replace(st, ".", "Unknown"), frac_df.index.values))
ax = axs[4]

previous_samples = 0
for alpha, color, mt in zip(alphas, colors, m_types):
    y = frac_df[f"{mt}_fraction"].values
    ax.bar(
        x,
        y,
        width = 0.85,
        bottom = previous_samples,
        color = color,
        alpha = alpha,
        label = mt
    )
    previous_samples = previous_samples + y

# Add number of sequences above each bar
for index, total in enumerate(frac_df["total"].values):
    ax.text(x=index, y=1.01, s="{:,}".format(total), size=fontsize, ha="center")

ax.xaxis.set_tick_params(labelbottom=False)
ax.yaxis.set_tick_params(labelleft=False)
ax.margins(x=subplt_spacing, y=0)
ax.spines[['left']].set_visible(False)
ax.set_xticks([])
ax.set_yticks([])
ax.patch.set_alpha(0)

# Add legend
ax.legend(bbox_to_anchor=(1.001, 1.025), loc="upper left", fontsize=fontsize, labels=legend_labels)


# Remove space between subplots
plt.subplots_adjust(wspace=0)


# Add grid
ax3 = fig.add_subplot(111, zorder=-1)
for _, spine in ax3.spines.items():
    spine.set_visible(False)
ax3.set_xticks([])
ax3.tick_params(labelleft=False, labelbottom=False, left=False, right=False)
# ax3.get_shared_y_axes().join(axs[0], axs[1], axs[2], axs[3], axs[4])
ax3.grid(color="lightgrey", ls="--", lw=1)

plt.savefig("tax_assignment_validation.png", dpi=300, bbox_inches="tight", transparent=True)
plt.savefig("tax_assignment_validation.svg", dpi=300, bbox_inches="tight", transparent=True)

fig.show()

<ipython-input-4-8dd307f433ed>:34: UserWarning: set_ticklabels() should only be used with a fixed number of ticks, i.e. after set_ticks() or using a FixedLocator.
  ax.set_xticklabels(x, rotation=45, ha="right")
<ipython-input-4-8dd307f433ed>:68: UserWarning: set_ticklabels() should only be used with a fixed number of ticks, i.e. after set_ticks() or using a FixedLocator.
  ax.set_xticklabels(x, rotation=45, ha="right")
<ipython-input-4-8dd307f433ed>:99: UserWarning: set_ticklabels() should only be used with a fixed number of ticks, i.e. after set_ticks() or using a FixedLocator.
  ax.set_xticklabels(x, rotation=45, ha="right")


Get total percentages at species-level:

In [5]:
species_df = pd.read_csv("species_mapping.csv")
species_df = species_df.set_index("mapping").sum(axis=1).to_frame().T
species_df

mapping  correct  incorrect  not_aligned  multimapped
0         287137         23         8266         1135

In [6]:
total = species_df.sum(axis=1).values[0]

for column in species_df.columns:
    print(f"% {column}: {(species_df[column].values[0] / total) * 100}")

print(total)

% correct: 96.82223893229386
% incorrect: 0.0077555713664305154
% not_aligned: 2.7872849093441143
% multimapped: 0.3827205869955928
296561
